## Library

In [1]:
import os
import numpy as np
import pandas as pd
import time
from rdkit import Chem
from rdkit.Chem import AllChem, Descriptors
from rdkit.ML.Descriptors import MoleculeDescriptors
from sklearn.ensemble import RandomForestRegressor
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.cross_decomposition import PLSRegression
from sklearn.neural_network import MLPRegressor
from sklearn.metrics import mean_squared_error, r2_score
from deap import base, creator, tools, algorithms

## Read File

In [5]:
import os

def read_data(base_dir):
    """Reads all files in subdirectories of the given directory.
    
    Parameters:
        base_dir (str): Base directory to read all files inside.

    Returns:
        dict: Include Compound ID as key and Smiles as value.
    
    """
    #Save values in dictionary
    data_contents = {}

    # Check every subdicrectories
    for dir_name in os.listdir(base_dir):
        sub_dir_path = os.path.join(base_dir, dir_name)

        if os.path.isdir(sub_dir_path):
            file_path = os.path.join(sub_dir_path, "daylight-smiles")
            if os.path.exists(file_path):
                with open(file_path, 'r', encoding='utf-8') as f:
                    data_contents[int(dir_name)] = f.read()  #Save file
    return data_contents

# Base directory
base_directory = "Data/compounds"

# Read all file
data_files_content = read_data(base_directory)


In [6]:
# Read file
df = pd.read_table('Data/properties/pIGC50/values')

# Change index 
df.set_index('Compound Id', inplace=True)

# Mapping df with Smiles data above base on Compound Id
df['Smiles'] = df.index.map(data_files_content)


In [7]:
df

pIGC50                                             Smiles
Compound Id                                                           
1             -0.16                                    C(Cl)(Cl)(Cl)Cl
2              1.64                                  C([N+](=O)[O-])Br
3             -2.72                                                 CO
4             -0.87                                            C(=O)NN
5             -1.32                                          C(=S)(N)N
...             ...                                                ...
1990           2.11           C1=CC=C(C=C1)C2=C(C(=CC=C2)C3=CC=CC=C3)O
1991           0.77         C1=CC=C(C=C1)P(=O)(C2=CC=CC=C2)C3=CC=CC=C3
1992           1.81      C1=CC=C(C=C1)OP(=O)(OC2=CC=CC=C2)OC3=CC=CC=C3
1993           0.36         CC(C)(C)C1=CC(=C(C(=C1)C(C)(C)C)O)C(C)(C)C
1994           1.70  C1=CC=C2C(=C1)C(=C(C(=O)O2)CC3=C(C4=CC=CC=C4OC...

[1994 rows x 2 columns]

In [8]:
# Function to canonicalize SMILES strings
def canonical_smiles(smiles_list):
    """
    Convert a list of SMILES strings to their canonical forms.

    Parameters:
        smiles_list (list): List of SMILES strings.

    Returns:
        list: Canonicalized SMILES strings.
    """
    canonicalized = []
    for smi in smiles_list:
        try:
            mol = Chem.MolFromSmiles(smi)
            if mol:
                canonicalized.append(Chem.MolToSmiles(mol))
            else:
                canonicalized.append(None)  # For invalid SMILES
        except Exception as e:
            canonicalized.append(None)  # Catch any exceptions
    return canonicalized

# Function to calculate RDKit molecular descriptors
def calculate_rdkit_descriptors(smiles_list):
    """
    Calculate molecular descriptors for a list of SMILES strings.

    Parameters:
        smiles_list (list): List of SMILES strings.

    Returns:
        tuple: A DataFrame of molecular descriptors and a list of descriptor names.
    """
    mols = [Chem.MolFromSmiles(smi) for smi in smiles_list if smi is not None]
    calc = MoleculeDescriptors.MolecularDescriptorCalculator([x[0] for x in Descriptors._descList])
    desc_names = calc.GetDescriptorNames()

    descriptors = []
    for mol in mols:
        try:
            # Add hydrogens to the molecule
            mol = Chem.AddHs(mol)
            # Calculate descriptors
            descriptors.append(calc.CalcDescriptors(mol))
        except Exception as e:
            descriptors.append([None] * len(desc_names))  # Handle errors by appending NaNs

    return pd.DataFrame(descriptors, columns=desc_names), desc_names


In [9]:
# Canonicalize SMILES strings
df['Canonical_SMILES'] = canonical_smiles(df['Smiles'])

# Calculate RDKit molecular descriptors
descriptors_df, descriptor_names = calculate_rdkit_descriptors(df['Canonical_SMILES'])

# Combine data with descriptors
result_df = pd.concat([df.reset_index(drop=True), descriptors_df], axis=1)

# Save the output to a CSV file

# output_file = 'pIGC50_descriptor.csv'
# result_df.to_csv(output_file, index=False)

# print(f"Descriptors saved to {output_file}")

[23:44:24] DEPRECATION WARNING: please use MorganGenerator
[23:44:24] DEPRECATION WARNING: please use MorganGenerator
[23:44:24] DEPRECATION WARNING: please use MorganGenerator
[23:44:24] DEPRECATION WARNING: please use MorganGenerator
[23:44:24] DEPRECATION WARNING: please use MorganGenerator
[23:44:24] DEPRECATION WARNING: please use MorganGenerator
[23:44:24] 

****
Pre-condition Violation
bad result vector size
Violation occurred on line 42 in file /private/var/folders/0n/_7v_bpwd1w71f8l0b0kjw5br0000gn/T/cirrus-ci-build/build/temp.macosx-11.0-arm64-cpython-311/rdkit/Code/GraphMol/Descriptors/Crippen.cpp
Failed Expression: logpContribs.size() == mol.getNumAtoms() && mrContribs.size() == mol.getNumAtoms()
****

[23:44:24] 

****
Pre-condition Violation
bad result vector size
Violation occurred on line 42 in file /private/var/folders/0n/_7v_bpwd1w71f8l0b0kjw5br0000gn/T/cirrus-ci-build/build/temp.macosx-11.0-arm64-cpython-311/rdkit/Code/GraphMol/Descriptors/Crippen.cpp
Failed Expressio

## Preprocssing

In [155]:
result_df = result_df.dropna(axis=1)

In [156]:
X = result_df.iloc[:, 4:]
y = result_df.iloc[:, :1]

In [157]:
scaler = StandardScaler()
X_std = scaler.fit_transform(X)

In [158]:
X_train, X_test, y_train, y_test = train_test_split(X_std, y.values, test_size=0.2, random_state=42)

## GA-MLR

In [146]:
# Genetic Algorithm parameters
n_population = 200  # Population size
n_generations = 100  # Number of generations

# Define the fitness function
def fitness(individual):
    selected_features = [i for i in range(len(individual)) if individual[i] == 1]
    if not selected_features:  # Penalize if no features are selected
        return 1e6,
    X_selected = X_train[:, selected_features]
    model = LinearRegression().fit(X_selected, y_train)
    y_pred = model.predict(X_selected)
    mse = mean_squared_error(y_train, y_pred)
    return mse,

# DEAP Setup
creator.create("FitnessMin", base.Fitness, weights=(-1.0,))  # Minimize MSE
creator.create("Individual", list, fitness=creator.FitnessMin)

toolbox = base.Toolbox()
toolbox.register("attr_bool", np.random.randint, 0, 2)
toolbox.register("individual", tools.initRepeat, creator.Individual, toolbox.attr_bool, n=X_train.shape[1])
toolbox.register("population", tools.initRepeat, list, toolbox.individual)

toolbox.register("evaluate", fitness)
toolbox.register("mate", tools.cxTwoPoint)
toolbox.register("mutate", tools.mutFlipBit, indpb=0.05)
toolbox.register("select", tools.selTournament, tournsize=3)

start_time = time.time()
# Run Genetic Algorithm
population = toolbox.population(n=n_population)
algorithms.eaSimple(population, toolbox, cxpb=0.5, mutpb=0.2, ngen=n_generations, verbose=True)

# Best solution
best_individual = tools.selBest(population, k=1)[0]
selected_features = [i for i, bit in enumerate(best_individual) if bit == 1]

print("Selected features indices:", selected_features)

# Evaluate the final model on the test set
X_train_selected = X_train[:, selected_features]
X_test_selected = X_test[:, selected_features]

final_model = LinearRegression().fit(X_train_selected, y_train)

end_time = time.time()
run_time_ga_mlr = end_time - start_time

y_pred_ga_mlr= final_model.predict(X_test_selected)

mse_ga_mlr = mean_squared_error(y_test, y_pred_ga_mlr)
r2_ga_mlr = r2_score(y_test, y_pred_ga_mlr)

print("MSE GA-MLR model:", mse_ga_mlr)
print("R2 GA-MLR model:", r2_ga_mlr)
print("Run time model:", run_time_ga_mlr, "seconds")


/opt/homebrew/anaconda3/lib/python3.11/site-packages/deap/creator.py:185: RuntimeWarning: A class named 'FitnessMin' has already been created and it will be overwritten. Consider deleting previous creation of that class or rename it.
  warnings.warn("A class named '{0}' has already been created and it "
/opt/homebrew/anaconda3/lib/python3.11/site-packages/deap/creator.py:185: RuntimeWarning: A class named 'Individual' has already been created and it will be overwritten. Consider deleting previous creation of that class or rename it.
  warnings.warn("A class named '{0}' has already been created and it "


gen	nevals
0  	200   
1  	106   
2  	129   
3  	120   
4  	119   
5  	122   
6  	126   
7  	114   
8  	117   
9  	123   
10 	126   
11 	128   
12 	131   
13 	117   
14 	129   
15 	120   
16 	125   
17 	121   
18 	121   
19 	115   
20 	115   
21 	128   
22 	105   
23 	109   
24 	137   
25 	123   
26 	119   
27 	105   
28 	136   
29 	113   
30 	126   
31 	124   
32 	114   
33 	109   
34 	125   
35 	128   
36 	132   
37 	122   
38 	120   
39 	131   
40 	124   
41 	112   
42 	115   
43 	132   
44 	133   
45 	115   
46 	130   
47 	134   
48 	113   
49 	112   
50 	126   
51 	118   
52 	112   
53 	127   
54 	125   
55 	115   
56 	118   
57 	120   
58 	144   
59 	121   
60 	118   
61 	131   
62 	124   
63 	112   
64 	124   
65 	122   
66 	116   
67 	128   
68 	102   
69 	114   
70 	123   
71 	114   
72 	123   
73 	118   
74 	129   
75 	119   
76 	131   
77 	109   
78 	128   
79 	122   
80 	122   
81 	133   
82 	119   
83 	136   
84 	108   
85 	106   
86 	118   
87 	121   
88 	107   
89 	128   

## PLS

In [147]:
#Call model with 50 components
pls = PLSRegression(n_components = 50) #can change n_components for better result

start_time = time.time()
#fit model
pls.fit(X_train, y_train)

end_time = time.time()

#predict
y_pred_pls= pls.predict(X_test)

#evaluate model
run_time_pls = end_time - start_time
mse_pls = mean_squared_error(y_test,y_pred_pls)
r2_pls = r2_score(y_test,y_pred_pls)

print(f"MSE PLS model: " ,mse_pls)
print(f"R2 PLS model: ", r2_pls)
print(f"Run time PLS model: ", run_time_pls)

MSE PLS model:  0.3420790046663141
R2 PLS model:  0.6756953945391982
Run time PLS model:  0.16741418838500977


## ANN

In [148]:
#Call model with (64,32) hidden layer
mlp = MLPRegressor(hidden_layer_sizes=(64,32))

start_time = time.time()

#fit model
mlp.fit(X_train, y_train)

end_time = time.time()

#predict
y_pred_mlp= mlp.predict(X_test)

#evalute model
run_time_mlp = end_time - start_time
mse_mlp = mean_squared_error(y_test,y_pred_mlp)
r2_mlp = r2_score(y_test,y_pred_mlp)

print(f"MSE ANN model: " ,mse_mlp)
print(f"R2 ANN model: ", r2_mlp)
print(f"Run time ANN model: ", run_time_mlp)

/opt/homebrew/anaconda3/lib/python3.11/site-packages/sklearn/neural_network/_multilayer_perceptron.py:1650: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


MSE ANN model:  0.3241068293991832
R2 ANN model:  0.6927337369389743
Run time ANN model:  2.9511468410491943


## Random Forest

In [149]:
#Call model
rf = RandomForestRegressor()

start_time = time.time()

#Fit model
rf.fit(X_train, y_train)

end_time = time.time()

#Predict
y_pred_rf= rf.predict(X_test)

#evalaute 
run_time_rf = end_time - start_time
mse_rf = mean_squared_error(y_test,y_pred_rf)
r2_rf = r2_score(y_test,y_pred_rf)

print(f"MSE Random Forest model: " ,mse_rf)
print(f"R2 Random Forest model: ", r2_rf)
print(f"Run time Random Forest model: ", run_time_rf)

/opt/homebrew/anaconda3/lib/python3.11/site-packages/sklearn/base.py:1389: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  return fit_method(estimator, *args, **kwargs)


MSE Random Forest model:  0.2675374211671122
R2 Random Forest model:  0.7463638029985631
Run time Random Forest model:  5.06289005279541


## Conclusion

In [167]:
# Tạo danh sách để lưu kết quả
models = []
mse_values = []
r2_values = []
run_times = []

In [168]:
models.extend(['GA-MLR', 'PLS', 'ANN', 'Random Forest'])
mse_values.extend([mse_ga_mlr, mse_pls, mse_mlp, mse_rf])
r2_values.extend([r2_ga_mlr,r2_pls,r2_mlp,r2_rf])
run_times.extend([run_time_ga_mlr,run_time_pls,run_time_mlp,run_time_pls])

In [169]:
# Tạo DataFrame kết quả
compare_df = pd.DataFrame({
    'Model': models,
    'MSE': mse_values,
    'R2': r2_values,
    'Run Time (s)': run_times
})

compare_df


Model       MSE        R2  Run Time (s)
0         GA-MLR  0.357092  0.661462    272.424271
1            PLS  0.342079  0.675695      0.167414
2            ANN  0.324107  0.692734      2.951147
3  Random Forest  0.267537  0.746364      0.167414